In [1]:
import numpy as np
import tensorflow as tf

In [2]:
tf.logging.set_verbosity(tf.logging.INFO)

In [3]:
#Let's create the model
def cnn_model_fn(features, labels, mode):
    #Input Lapyer
    input_layer = tf.reshape(features["x"], [-1,28,28,1]) 
    #batch_size=-1, the dimension should be dynamically computed. based on number of input values in features["x"]                                                          
    
    #CN layer 1
    conv1 = tf.layers.conv2d(inputs=input_layer, filters=32, kernel_size=[5,5], padding="same", activation=tf.nn.relu)
    
    #Pooling layer1
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2,2], strides=2)
    
    #CN layer 2
    conv2 = tf.layers.conv2d(inputs=pool1, filters=64, kernel_size=[5,5], padding="same", activation=tf.nn.relu)
    
    #pool layer2
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2,2], strides=2)
    
    #Dense Layer
    pool2_flat = tf.reshape(pool2, [-1, 7*7*64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)
    #Drop-out will only be applied if we are in training mode, mode==tf.estimator.ModKeys.TRAIN
    
    #Logits Layer
    logits = tf.layers.dense(inputs=dropout, units=10)
    #This has shape of batch_size(that -1),10
    #This returns batch-size,10 dimensional tensor
    
    predictions = {
        # Generate predictions (for PREDICT and EVAL mode)
        "classes": tf.argmax(input=logits, axis=1), #Simply findout which one has the maximum of 10
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor") #This one is the softmax
    }
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)
    #Estimator spec which says for this mode these are the predictions

    #Calculate loss - LOSS
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)
    
    # Configure the Training Op (for TRAIN mode) Optimizer
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode) Evalution Matric
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
            labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
        mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


In [4]:
def main(unused_arg):
    #Load training and eval data
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images #returns an np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    
    #Creating the extimator
    mnist_classiier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="/tmp/mnist_cnn_model")
    
    #Setting up some logging
    tensor_to_log = {"probabilities":"softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(tensors=tensor_to_log, every_n_iter=50)
    #We store a dict of the tensors we want to log in tensor_to_log
    #Each key is a label of our choice that will be printed in the log output, 
    #and the corresponding label is the name of a Tensor in the TensorFlow graph. 
    #Here, our probabilities can be found in softmax_tensor
    
    #Setting up some logging
    tensor_to_log = {"probabilities":"softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(tensors=tensor_to_log, every_n_iter=50)
    #We store a dict of the tensors we want to log in tensor_to_log
    #Each key is a label of our choice that will be printed in the log output, 
    #and the corresponding label is the name of a Tensor in the TensorFlow graph. 
    #Here, our probabilities can be found in softmax_tensor
    
    #Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(x={"x":train_data}, y=train_labels, batch_size=100, num_epochs=None, shuffle=True)
    mnist_classiier.train(input_fn=train_input_fn, steps=20000, hooks=[logging_hook])
    
    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": eval_data},
        y=eval_labels,
        num_epochs=1,
        shuffle=False)
    eval_results = mnist_classiier.evaluate(input_fn=eval_input_fn)
    print(eval_results)

if __name__ == "__main__":
    tf.app.run()

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_cnn_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f61b29db5c0>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_cnn_model/model.ckpt.
INFO:tensorflow:probabilities = [[ 0.09536913  0.10070458  0.12025649  0.09873686  0.1047031   0.104

INFO:tensorflow:loss = 2.30416, step = 1
INFO:tensorflow:probabilities = [[ 0.10646233  0.08702688  0.10250749  0.08746539  0.11137369  0.09345265
   0.11862417  0.12044034  0.06827093  0.10437614]
 [ 0.11450145  0.09376968  0.1058061   0.10357754  0.11802274  0.09583624
   0.106709    0.09204175  0.07356501  0.09617043]
 [ 0.10718404  0.10603885  0.10875266  0.10420272  0.0983983   0.09622398
   0.10794859  0.09993104  0.0867633   0.08455651]
 [ 0.1043341   0.09892643  0.11662775  0.09706999  0.10042433  0.09246562
   0.09857716  0.09705715  0.09776835  0.09674908]
 [ 0.10361645  0.10655151  0.10205848  0.09239461  0.1020521   0.09861609
   0.09676039  0.10103566  0.09700535  0.0999093 ]
 [ 0.10386382  0.10583577  0.10403171  0.09622613  0.10127854  0.09808721
   0.09908985  0.09826422  0.09496158  0.09836116]
 [ 0.11574183  0.09391902  0.11123253  0.09473354  0.11154621  0.10424361
   0.09767385  0.08745099  0.08299033  0.10046808]
 [ 0.10853205  0.09605709  0.11877377  0.09016267  0

INFO:tensorflow:global_step/sec: 63.1225
INFO:tensorflow:probabilities = [[ 0.10925645  0.10251309  0.11703069  0.09548787  0.09671246  0.09555795
   0.09813655  0.1061312   0.09030877  0.08886504]
 [ 0.11562951  0.10923021  0.10546101  0.09242214  0.10001674  0.09428268
   0.10007019  0.0932884   0.08812734  0.1014718 ]
 [ 0.10105565  0.10501442  0.09902018  0.10113147  0.10384571  0.09721129
   0.10248255  0.09206431  0.10356726  0.09460719]
 [ 0.10123158  0.08921758  0.12643516  0.10047105  0.10810516  0.1156155
   0.09941091  0.09473918  0.08005551  0.08471843]
 [ 0.12966399  0.11291989  0.10237648  0.1026395   0.08131993  0.08727216
   0.10517576  0.09144183  0.08927044  0.09792004]
 [ 0.11118665  0.09767132  0.10256864  0.10712577  0.09482314  0.10909237
   0.10301606  0.08729501  0.09863633  0.08858465]
 [ 0.1028491   0.10083286  0.11601574  0.08705989  0.10816979  0.10166162
   0.10813707  0.08660799  0.09830459  0.09036139]
 [ 0.11124016  0.10512707  0.11068617  0.09771851  0.

INFO:tensorflow:loss = 2.27921, step = 101 (1.582 sec)
INFO:tensorflow:probabilities = [[ 0.11969103  0.09006743  0.10283864  0.09336492  0.10506998  0.09129483
   0.10762465  0.10092615  0.09150332  0.09761902]
 [ 0.11933738  0.09721798  0.10976625  0.10799257  0.09204271  0.0942992
   0.10098951  0.0939198   0.09691279  0.08752178]
 [ 0.10212828  0.08793573  0.13688272  0.10246589  0.0919842   0.09271885
   0.10743453  0.08833922  0.0810924   0.10901817]
 [ 0.10065173  0.1024566   0.10474904  0.09561057  0.10572732  0.10188417
   0.10080912  0.08850335  0.0973485   0.10225963]
 [ 0.10610106  0.10227965  0.09974926  0.1023415   0.09702268  0.09935824
   0.09704435  0.10046708  0.10393742  0.09169881]
 [ 0.10673966  0.09355111  0.11537503  0.09464099  0.10503008  0.0953299
   0.11724681  0.08852836  0.08655643  0.09700161]
 [ 0.10833847  0.10131075  0.10144218  0.11014518  0.08883279  0.11059026
   0.09850835  0.08781609  0.09688151  0.09613442]
 [ 0.1003065   0.10610884  0.09107767  0

INFO:tensorflow:global_step/sec: 72.1797
INFO:tensorflow:probabilities = [[ 0.1050945   0.10138515  0.10881157  0.09122773  0.10800555  0.10718616
   0.09654427  0.1033693   0.09031005  0.08806568]
 [ 0.1013537   0.09890871  0.10428317  0.08781518  0.11165865  0.09363005
   0.10822073  0.09579792  0.0986468   0.09968504]
 [ 0.09706923  0.10649264  0.12643126  0.10081203  0.09739323  0.09066276
   0.09732307  0.09106596  0.10438953  0.08836031]
 [ 0.11036299  0.08430429  0.1062822   0.0940506   0.11128956  0.10250457
   0.10249485  0.09642185  0.09057529  0.10171377]
 [ 0.11372437  0.10533442  0.11184323  0.09690444  0.09290136  0.10559508
   0.10245943  0.09531866  0.07984572  0.09607323]
 [ 0.11157893  0.10095218  0.10204792  0.10026892  0.09658879  0.09556857
   0.10607383  0.09141366  0.09407008  0.10143709]
 [ 0.0971603   0.10138102  0.11844688  0.09253347  0.11357208  0.10349153
   0.09063536  0.08727506  0.10841863  0.08708568]
 [ 0.11888398  0.09538266  0.10952053  0.08812752  0

...

INFO:tensorflow:global_step/sec: 72.0242
INFO:tensorflow:probabilities = [[ 0.00000026  0.00003632  0.00007887  0.00000156  0.00008349  0.0001407
   0.99962699  0.00000003  0.00003171  0.00000008]
 [ 0.90369225  0.00000557  0.0048011   0.00111954  0.0013399   0.00691784
   0.07392116  0.00560046  0.00006098  0.00254124]
 [ 0.99984503  0.0000001   0.00006692  0.00000074  0.00000001  0.00006239
   0.00000191  0.00000054  0.00000091  0.00002142]
 [ 0.00017059  0.00010169  0.00349646  0.00634038  0.0000211   0.00020523
   0.00000522  0.00022231  0.98832661  0.00111049]
 [ 0.04824757  0.00278981  0.03026636  0.04140957  0.00110087  0.06662825
   0.00021992  0.61535192  0.02105392  0.17293175]
 [ 0.0010799   0.00028079  0.00059132  0.92324901  0.000027    0.07388679
   0.00047874  0.00004414  0.00024053  0.00012178]
 [ 0.00000001  0.00000164  0.99640816  0.00358612  0.          0.00000003
   0.          0.00000389  0.00000008  0.        ]
 [ 0.00005082  0.00004467  0.0045499   0.05015681  0.

INFO:tensorflow:loss = 0.0996802, step = 19901 (1.386 sec)
INFO:tensorflow:probabilities = [[ 0.99978858  0.00000003  0.00012645  0.00000007  0.00000001  0.00002062
   0.00006384  0.00000014  0.00000013  0.00000016]
 [ 0.9995448   0.00000003  0.00033721  0.00000487  0.00000001  0.00010853
   0.00000108  0.00000287  0.00000003  0.0000006 ]
 [ 0.00000017  0.00000002  0.00000514  0.00000001  0.00000214  0.00000015
   0.99999225  0.          0.00000008  0.        ]
 [ 0.00036993  0.98968703  0.00002504  0.00008724  0.00164545  0.00002638
   0.0002082   0.00024846  0.00748068  0.00022148]
 [ 0.00001785  0.98084176  0.00270646  0.00055005  0.00290075  0.00000265
   0.00001889  0.01197817  0.00001972  0.00096358]
 [ 0.00000745  0.00001556  0.99796104  0.00159475  0.00009882  0.00002089
   0.00004966  0.00001863  0.00020102  0.00003227]
 [ 0.00000002  0.00001667  0.99927098  0.00070744  0.00000001  0.00000132
   0.00000028  0.00000031  0.00000293  0.        ]
 [ 0.00074164  0.00000669  0.00038

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_cnn_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.132293.
INFO:tensorflow:Starting evaluation at 2018-02-22-01:10:01
INFO:tensorflow:Restoring parameters from /tmp/mnist_cnn_model/model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-02-22-01:10:01
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9688, global_step = 20000, loss = 0.101661
{'accuracy': 0.96880001, 'loss': 0.10166109, 'global_step': 20000}


SystemExit: 

/home/SONY/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2889: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [5]:
%tb

SystemExit: 